In [ ]:
%reload_ext autoreload
%autoreload 2
%matplotlib inline
%cd DeepLearning_Financial

## EXTERNAL
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import sklearn
import yfinance
from pandas import Series
from sklearn.preprocessing import PolynomialFeatures, StandardScaler, MinMaxScaler
from sklearn.pipeline import Pipeline
from sklearn.model_selection import TimeSeriesSplit, PredefinedSplit
from sklearn.metrics import make_scorer
from sklearn.model_selection import cross_validate
from sklearn.model_selection import GridSearchCV
from IPython.display import display
import datetime
import torch
import torch.nn as nn
from torch.autograd import Variable
import torch.optim as optim
from torch.utils.data import Dataset, DataLoader
import torch.nn.functional as F
import numpy as np
import time
import os
import random 
from sklearn.datasets import make_regression
from torch import nn
import torch.nn.functional as F
from skorch import NeuralNetRegressor
from torch.nn.modules.loss import MSELoss
import tensorflow as tf
from tensorflow import keras
from skorch.dataset import CVSplit
from skorch import callbacks
import pickle
from sklearn.model_selection import train_test_split
from functools import partial
import skorch
import pywt
from sklearn import preprocessing
import joblib


##INTERNAL
from models import Autoencoder, waveletSmooth, SequenceDouble, SequenceDoubleAtt, SequenceAtt
from utils import prepare_data_lstm, ExampleDataset, save_checkpoint, evaluate_lstm, backtest
from testing import *
from sa_tools import *
from test_models import *



#creazione dataset
# indices = ['^DJI', '^GSPC', '^HSI', '^N225', 'ASHR','^NSEI']
indices = ['^GSPC']
feature_sets = ['open', 'ohlcv', 'ext']
start_date="2000-01-01"
end_date="2018-12-31"

# datasets=get_datasets(indices = indices, feature_sets = feature_sets, end_date=end_date, start_date=start_date)
# save(datasets, 'datasets')
datasets = load('^GSCP')
tss = TimeSeriesSplit(4)
tss_split = CVSplit(cv=tss, stratified=False, random_state=None)

for index in indices:
    X=datasets[index]["target"]
    for i, (train, val) in enumerate(tss.split(X), start=1):
        print("FOLD {}".format(i))
        train_dates = X.index[train]
        val_dates = X.index[val]
        print("Training set da {} a {}".format(train_dates.min(), train_dates.max()))
        print("Validation set da {} a {}".format(val_dates.min(), val_dates.max()))
        print(X.index.min())
        print(X.index.max())
    for i, (train_dates, val_dates) in enumerate(tss.split(datasets[index]["target"]), start=1):
        for model_name in get_model_names():
            
            # get the model
            save_name = "{}_{}_{}_{}.pkl".format(model_name, index, datasets[index]["target"].index[train_dates].min().date(), datasets[index]["target"].index[train_dates].max().date())
            print(save_name)
            model, feature_set = get_model(model_name,  save_name)
                
            #get the dataset
            sa=None
            ld=False
            fset= feature_set
            if(feature_set is 'ext_sa'):
                fset='ext'
                sa = "sa_{}_{}_{}".format(index, datasets[index]["target"][train_dates].index.min().date(), datasets[index]["target"][train_dates].index.max().date())
            x, y, x_train, x_val, x_scaler, y_train, y_val, y_scaler = get_dataset_train(datasets=datasets, feature_set=fset, train_dates=train_dates, val_dates=val_dates, index=index, sa=sa, ld=ld)
            
            
            #prepare dataset for training
            n_days=5

            x_batch = days_group(x, n_days=n_days)
            y_batch = y[n_days:]
            serie = x_batch
            train_dates_s = train_dates[n_days:].copy()
            val_dates_s = val_dates.copy()

            splitted = np.split(serie, [len(train_dates_s)])
            l1, l2 = len(splitted[0]), len(splitted[1])
            train_s = PredefinedSplit(np.concatenate((np.ones(l1)*-1,np.ones(l2))))
            train_split =  CVSplit(cv=train_s, stratified=False, random_state=None)  
            train_dates_s, val_dates_s = list(train_s.split(serie))[0]
            
            model.train_split = train_split
            model.fit(x_batch,y_batch)
    

/data/home/dsvm_server_admin/notebooks/fastai/tesi/DeepLearning_Financial
FOLD 1
Training set da 2000-09-19 00:00:00 a 2004-05-18 00:00:00
Validation set da 2004-05-19 00:00:00 a 2008-01-12 00:00:00
2000-09-19 00:00:00
2018-12-27 00:00:00
FOLD 2
Training set da 2000-09-19 00:00:00 a 2008-01-12 00:00:00
Validation set da 2008-01-13 00:00:00 a 2011-09-07 00:00:00
2000-09-19 00:00:00
2018-12-27 00:00:00
FOLD 3
Training set da 2000-09-19 00:00:00 a 2011-09-07 00:00:00
Validation set da 2011-09-08 00:00:00 a 2015-05-03 00:00:00
2000-09-19 00:00:00
2018-12-27 00:00:00
FOLD 4
Training set da 2000-09-19 00:00:00 a 2015-05-03 00:00:00
Validation set da 2015-05-04 00:00:00 a 2018-12-27 00:00:00
2000-09-19 00:00:00
2018-12-27 00:00:00
lstm_sa_^GSPC_2000-09-19_2004-05-18.pkl
Data Shuffled
Epoch 1/15000 | train loss: 6.6380 | train_error 0.7747 | valid_error 1.2518
Data Shuffled
Epoch 2/15000 | train loss: 7.2104 | train_error 0.6661 | valid_error 1.1469
Data Shuffled
Epoch 3/15000 | train loss: 8.

Epoch 84/15000 | train loss: 5.1175 | train_error 0.1090 | valid_error 0.5589
Data Shuffled
Epoch 85/15000 | train loss: 5.1141 | train_error 0.1086 | valid_error 0.5531
Data Shuffled
Epoch 86/15000 | train loss: 5.1500 | train_error 0.1080 | valid_error 0.5518
Data Shuffled
Epoch 87/15000 | train loss: 5.1418 | train_error 0.1072 | valid_error 0.5524
Data Shuffled
Epoch 88/15000 | train loss: 5.1132 | train_error 0.1061 | valid_error 0.5454
Data Shuffled
Epoch 89/15000 | train loss: 5.1366 | train_error 0.1056 | valid_error 0.5404
Data Shuffled
Epoch 90/15000 | train loss: 5.1274 | train_error 0.1045 | valid_error 0.5394
Data Shuffled
Epoch 91/15000 | train loss: 5.1482 | train_error 0.1043 | valid_error 0.5307
Data Shuffled
Epoch 92/15000 | train loss: 5.1307 | train_error 0.1033 | valid_error 0.5354
Data Shuffled
Epoch 93/15000 | train loss: 5.1235 | train_error 0.1029 | valid_error 0.5282
Data Shuffled
Epoch 94/15000 | train loss: 5.1198 | train_error 0.1017 | valid_error 0.5279
Da

Epoch 173/15000 | train loss: 5.2675 | train_error 0.0699 | valid_error 0.3897
Data Shuffled
Epoch 174/15000 | train loss: 5.2585 | train_error 0.0681 | valid_error 0.3879
Data Shuffled
Epoch 175/15000 | train loss: 5.2652 | train_error 0.0680 | valid_error 0.3886
Data Shuffled
Epoch 176/15000 | train loss: 5.2763 | train_error 0.0684 | valid_error 0.3774
Data Shuffled
Epoch 177/15000 | train loss: 5.2694 | train_error 0.0686 | valid_error 0.3788
Data Shuffled
Epoch 178/15000 | train loss: 5.2464 | train_error 0.0672 | valid_error 0.3854
Data Shuffled
Epoch 179/15000 | train loss: 5.2578 | train_error 0.0677 | valid_error 0.3904
Data Shuffled
Epoch 180/15000 | train loss: 5.2580 | train_error 0.0672 | valid_error 0.3847
Data Shuffled
Epoch 181/15000 | train loss: 5.2632 | train_error 0.0685 | valid_error 0.3770
Data Shuffled
Epoch 182/15000 | train loss: 5.2664 | train_error 0.0670 | valid_error 0.3797
Data Shuffled
Epoch 183/15000 | train loss: 5.2556 | train_error 0.0668 | valid_erro

Epoch 263/15000 | train loss: 5.2265 | train_error 0.0593 | valid_error 0.3482
Data Shuffled
Epoch 264/15000 | train loss: 5.2464 | train_error 0.0591 | valid_error 0.3321
Data Shuffled
Epoch 265/15000 | train loss: 5.2365 | train_error 0.0585 | valid_error 0.3380
Data Shuffled
Epoch 266/15000 | train loss: 5.2384 | train_error 0.0585 | valid_error 0.3419
Data Shuffled
Epoch 267/15000 | train loss: 5.2425 | train_error 0.0595 | valid_error 0.3336
Data Shuffled
Epoch 268/15000 | train loss: 5.2439 | train_error 0.0585 | valid_error 0.3345
Data Shuffled
Epoch 269/15000 | train loss: 5.2464 | train_error 0.0588 | valid_error 0.3396
Data Shuffled
Epoch 270/15000 | train loss: 5.2412 | train_error 0.0585 | valid_error 0.3392
Data Shuffled
Epoch 271/15000 | train loss: 5.2505 | train_error 0.0587 | valid_error 0.3320
Data Shuffled
Epoch 272/15000 | train loss: 5.2335 | train_error 0.0585 | valid_error 0.3429
Data Shuffled
Epoch 273/15000 | train loss: 5.2437 | train_error 0.0586 | valid_erro

Epoch 353/15000 | train loss: 5.3131 | train_error 0.0543 | valid_error 0.3216
Data Shuffled
Epoch 354/15000 | train loss: 5.3081 | train_error 0.0547 | valid_error 0.3143
Data Shuffled
Epoch 355/15000 | train loss: 5.2988 | train_error 0.0540 | valid_error 0.3144
Data Shuffled
Epoch 356/15000 | train loss: 5.3103 | train_error 0.0549 | valid_error 0.3144
Data Shuffled
Epoch 357/15000 | train loss: 5.3154 | train_error 0.0547 | valid_error 0.3180
Data Shuffled
Epoch 358/15000 | train loss: 5.3142 | train_error 0.0542 | valid_error 0.3087
Data Shuffled
Epoch 359/15000 | train loss: 5.3128 | train_error 0.0542 | valid_error 0.3104
Data Shuffled
Epoch 360/15000 | train loss: 5.3119 | train_error 0.0537 | valid_error 0.3149
Data Shuffled
Epoch 361/15000 | train loss: 5.3167 | train_error 0.0541 | valid_error 0.3151
Data Shuffled
Epoch 362/15000 | train loss: 5.3185 | train_error 0.0539 | valid_error 0.3161
Data Shuffled
Epoch 363/15000 | train loss: 5.3152 | train_error 0.0538 | valid_erro

...

/data/anaconda/envs/fastai/lib/python3.6/site-packages/torch/storage.py:34: FutureWarning: pickle support for Storage will be removed in 1.5. Use `torch.save` instead
  warnings.warn("pickle support for Storage will be removed in 1.5. Use `torch.save` instead", FutureWarning)


    891                    -0.8882  -0.4226        0.0309        1.0702        5.2142
    892                    -0.9852  -0.7341        0.0411        1.3045        2.3056
    893                    -1.0005  -0.7727        0.0423        1.3336        1.6763
    894                    -0.9805  -0.7383        0.0384        1.3077        2.3128
    895                    -0.9435  -0.5841        0.0354        1.1917        2.1524
    896                    -0.8868  -0.3977        0.0325        1.0515        2.5903
    897                    -0.8681  -0.3649        0.0322        1.0268        2.1111
    898                    -0.8503  -0.3405        0.0305        1.0085        2.4098
    899                    -0.8349  -0.3026        0.0289        0.9799        2.1637
    900                    -0.8122  -0.2482        0.0304        0.9390        2.1318
    901                    -0.8177  -0.2691        0.0282        0.9548        4.0976
    902                    -0.8122  -0.2622        0.0

/data/anaconda/envs/fastai/lib/python3.6/site-packages/torch/storage.py:34: FutureWarning: pickle support for Storage will be removed in 1.5. Use `torch.save` instead
  warnings.warn("pickle support for Storage will be removed in 1.5. Use `torch.save` instead", FutureWarning)


    908                    -0.8790  -0.4822        0.0286        1.1150        2.3246
    909                    -0.8752  -0.4571        0.0497        1.0962        2.1875
    910                    -0.8924  -0.5113        0.0462        1.1369        2.4510
    911                    -0.8571  -0.4184        0.0441        1.0671        2.3931
    912                    -0.9047  -0.5946        0.0392        1.1996        2.4957
    913                    -0.8980  -0.5578        0.0447        1.1719        1.5960
    914                    -0.9068  -0.5899        0.0433        1.1961        2.6949
    915                    -0.9256  -0.6653        0.0417        1.2528        1.3984
    916                    -0.9356  -0.7076        0.0409        1.2846        2.1550
    917                    -0.9485  -0.7645        0.0439        1.3274        2.1606
    918                    -0.8903  -0.5381        0.0434        1.1571        2.0446
    919                    -0.7423  -0.0614        0.0

   1004                    -0.8823  -0.5066        0.0300        1.1334        2.1354
